In [1]:
import pandas as pd
import numpy as np
from sklearn.neighbors import NearestNeighbors

In [2]:
data = pd.read_feather('database/GS.feather')

In [3]:
def rfm_variables(df):
    f_sales = len(df)
    f_profit = len(df[df['Profit'] > 0])
    m_sales = round(df['Sales'].sum(),2)
    m_profit = round(df['Profit'].sum(),2)
    m_qty = df['Quantity'].sum()
    m_deliver = round(df['Shipping Cost'].sum(),2)
    df_sort = df[['Order Date']].sort_values(by='Order Date').drop_duplicates()
    df_sort['diff'] = df_sort['Order Date'] - df_sort['Order Date'].shift(1)
    df_sort['diff_int'] = df_sort['diff'].dt.days
    r_days = round(df_sort['diff_int'].mean(),2)
    return f_sales, f_profit, m_sales, m_profit, m_qty, m_deliver, r_days

In [4]:
def fit_data(data, variable):
    rfm = pd.DataFrame()
    variaveis = data[variable].unique()
    for variavel in variaveis:
        dados = data[data[variable] == variavel]
        f_vendas, f_lucro, m_vendas, m_lucro, m_qtde, m_entrega, r_dias = rfm_variables(dados)
        new_row = {
            'referencia': variavel,
            'm_vendas': m_vendas,
            'm_lucro': m_lucro,
            'm_qtde': m_qtde,
            'm_entrega': m_entrega,
            'r_dias': r_dias,
            'f_vendas': f_vendas,
            'f_lucro': f_lucro
        }
        rfm = rfm.append(
            new_row,
            ignore_index = True
        )
    return rfm

In [9]:
original = fit_data(data, 'Country')
original = original.fillna(0)
original

/tmp/ipykernel_2533/952877166.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rfm = rfm.append(
/tmp/ipykernel_2533/952877166.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rfm = rfm.append(
/tmp/ipykernel_2533/952877166.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rfm = rfm.append(
/tmp/ipykernel_2533/952877166.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rfm = rfm.append(
/tmp/ipykernel_2533/952877166.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rfm = rfm.append(
/tmp/ipykernel_2533/952877166.py:17: FutureWarning

referencia   m_vendas    m_lucro  m_qtde  m_entrega  r_dias  \
0               Mexico  622590.62  102818.10   10011   67658.40    1.89   
1             Colombia   81502.53   18798.05    1277    9411.77    9.32   
2               Brazil  361106.42   30090.50    6148   38170.04    2.66   
3            Nicaragua  149687.06   33401.44    2235   17155.17    5.30   
4               Panama   51539.93  -17723.45    1426    5416.04    7.78   
..                 ...        ...        ...     ...        ...     ...   
142           Ethiopia     850.62     290.16      18      81.54  358.67   
143  Equatorial Guinea     150.51      44.46       3       9.38    0.00   
144            Bahrain     669.18      12.84       6      72.76    0.00   
145               Chad    1317.03      90.00      11     297.94    0.00   
146            Eritrea     187.74      76.20       4       8.55    0.00   

     f_vendas  f_lucro  
0        2644     2272  
1         360      350  
2        1599     1185  
3         614      600  
4         388       75  
..        ...      ...  
142         7        7  
143         3        3  
144         2        2  
145         2        1  
146         2        2  

[147 rows x 8 columns]

In [14]:
variaveis = ['m_vendas', 'm_lucro', 'm_qtde', 'm_entrega', 'r_dias', 'f_vendas', 'f_lucro']

In [17]:
base = original[variaveis]
base

m_vendas    m_lucro  m_qtde  m_entrega  r_dias  f_vendas  f_lucro
0    622590.62  102818.10   10011   67658.40    1.89      2644     2272
1     81502.53   18798.05    1277    9411.77    9.32       360      350
2    361106.42   30090.50    6148   38170.04    2.66      1599     1185
3    149687.06   33401.44    2235   17155.17    5.30       614      600
4     51539.93  -17723.45    1426    5416.04    7.78       388       75
..         ...        ...     ...        ...     ...       ...      ...
142     850.62     290.16      18      81.54  358.67         7        7
143     150.51      44.46       3       9.38    0.00         3        3
144     669.18      12.84       6      72.76    0.00         2        2
145    1317.03      90.00      11     297.94    0.00         2        1
146     187.74      76.20       4       8.55    0.00         2        2

[147 rows x 7 columns]

In [18]:
vizinhos = NearestNeighbors(n_neighbors=min(4, len(base))).fit(base)
similares = pd.DataFrame()
for index, row in original.iterrows():
    print('Referencia: {0}'.format(row['referencia']))
    print('Referencias Similares:')
    original_referencia = original[original['referencia'] == row['referencia']][variaveis]
    similar = vizinhos.kneighbors(original_referencia, return_distance=False)[0]
    original_similar = original.iloc[similar][variaveis].reset_index()
    referencia = original.iloc[similar]['referencia'].reset_index()
    referencia = referencia.merge(original_similar, on='index', how='left')
    referencia = referencia.drop(columns=['index'])
    for ind, rw in referencia.iterrows():    
        if row['referencia'] != rw['referencia']:            
            print('--> {0}'.format(rw['referencia']))
            similares = similares.append({'referencia': row['referencia'], 'vizinho': rw['referencia']}, ignore_index = True)
similares

Referencia: Mexico
Referencias Similares:
--> Germany
--> India
--> China
Referencia: Colombia
Referencias Similares:
--> Saudi Arabia
--> Egypt
--> Bangladesh
Referencia: Brazil
Referencias Similares:
--> Indonesia
--> Italy
--> Spain
Referencia: Nicaragua
Referencias Similares:
--> Cuba
--> Guatemala
--> New Zealand
Referencia: Panama
Referencias Similares:
--> Argentina
--> Pakistan
--> South Korea
Referencia: Chile
Referencias Similares:
--> Algeria
--> Romania
--> Singapore
Referencia: Honduras
Referencias Similares:
--> Netherlands
--> Thailand
--> Pakistan
Referencia: Cuba
Referencias Similares:
--> Nicaragua
--> El Salvador
--> New Zealand
Referencia: Dominican Republic
Referencias Similares:
--> Guatemala
--> Iran
--> Japan
Referencia: Peru
Referencias Similares:
--> Ireland
--> Portugal
--> Haiti
Referencia: Guatemala
Referencias Similares:
--> Iran
--> Nicaragua
--> Cuba
Referencia: Argentina
Referencias Similares:
--> Pakistan
--> Panama
--> Vietnam
Referencia: Venezuela
Re

/tmp/ipykernel_2533/4098855849.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  similares = similares.append({'referencia': row['referencia'], 'vizinho': rw['referencia']}, ignore_index = True)
/tmp/ipykernel_2533/4098855849.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  similares = similares.append({'referencia': row['referencia'], 'vizinho': rw['referencia']}, ignore_index = True)
/tmp/ipykernel_2533/4098855849.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  similares = similares.append({'referencia': row['referencia'], 'vizinho': rw['referencia']}, ignore_index = True)
/tmp/ipykernel_2533/4098855849.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future vers

--> Madagascar
--> Hungary
--> Bolivia
Referencia: Trinidad and Tobago
Referencias Similares:
--> Barbados
--> Niger
--> Jordan
Referencia: Guadeloupe
Referencias Similares:
--> Slovenia
--> Gabon
--> Tunisia
Referencia: United Kingdom
Referencias Similares:
--> India
--> Mexico
--> Germany
Referencia: France
Referencias Similares:
--> Australia
--> China
--> Germany
Referencia: Germany
Referencias Similares:
--> Mexico
--> India
--> China
Referencia: Italy
Referencias Similares:
--> Spain
--> Brazil
--> Philippines
Referencia: Spain
Referencias Similares:
--> Italy
--> Brazil
--> El Salvador
Referencia: Netherlands
Referencias Similares:
--> Honduras
--> Pakistan
--> Argentina
Referencia: Sweden
Referencias Similares:
--> South Korea
--> Venezuela
--> Myanmar (Burma)
Referencia: Belgium
Referencias Similares:
--> Poland
--> Singapore
--> Romania
Referencia: Austria
Referencias Similares:
--> South Africa
--> Morocco
--> Democratic Republic of the Congo
Referencia: Ireland
Referencias 

/tmp/ipykernel_2533/4098855849.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  similares = similares.append({'referencia': row['referencia'], 'vizinho': rw['referencia']}, ignore_index = True)
/tmp/ipykernel_2533/4098855849.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  similares = similares.append({'referencia': row['referencia'], 'vizinho': rw['referencia']}, ignore_index = True)
/tmp/ipykernel_2533/4098855849.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  similares = similares.append({'referencia': row['referencia'], 'vizinho': rw['referencia']}, ignore_index = True)
/tmp/ipykernel_2533/4098855849.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future vers

--> France
--> China
--> Germany
Referencia: Indonesia
Referencias Similares:
--> Brazil
--> Italy
--> Spain
Referencia: Vietnam
Referencias Similares:
--> Thailand
--> Malaysia
--> Argentina
Referencia: Malaysia
Referencias Similares:
--> Canada
--> Iraq
--> Belgium
Referencia: Thailand
Referencias Similares:
--> Vietnam
--> Argentina
--> Pakistan
Referencia: Cambodia
Referencias Similares:
--> Kenya
--> Sudan
--> Bulgaria
Referencia: Pakistan
Referencias Similares:
--> Argentina
--> Panama
--> Vietnam
Referencia: Myanmar (Burma)
Referencias Similares:
--> Chile
--> Romania
--> Tanzania
Referencia: South Korea
Referencias Similares:
--> Sweden
--> Venezuela
--> Myanmar (Burma)
Referencia: Nepal
Referencias Similares:
--> Guinea
--> Liberia
--> Albania
Referencia: Afghanistan
Referencias Similares:
--> Mozambique
--> Cameroon
--> Norway
Referencia: Bangladesh
Referencias Similares:
--> Colombia
--> Saudi Arabia
--> Russia
Referencia: Hong Kong
Referencias Similares:
--> Qatar
--> Benin

...

--> Djibouti
--> Sierra Leone
--> Paraguay
Referencia: Kyrgyzstan
Referencias Similares:
--> Rwanda
--> Georgia
--> Moldova
Referencia: Mali
Referencias Similares:
--> Czech Republic
--> Uruguay
--> Libya
Referencia: Syria
Referencias Similares:
--> Moldova
--> Georgia
--> Rwanda
Referencia: Hungary
Referencias Similares:
--> Ecuador
--> Bulgaria
--> Belarus
Referencia: Namibia
Referencias Similares:
--> Lebanon
--> Bosnia and Herzegovina
--> Paraguay
Referencia: Republic of the Congo
Referencias Similares:
--> Central African Republic
--> Paraguay
--> Sierra Leone
Referencia: Armenia
Referencias Similares:
--> Burundi
--> Macedonia
--> Swaziland
Referencia: Slovenia
Referencias Similares:
--> Guadeloupe
--> Gabon
--> Tunisia
Referencia: Macedonia
Referencias Similares:
--> Armenia
--> Burundi
--> Eritrea
Referencia: Uganda
Referencias Similares:
--> Turkmenistan
--> Yemen
--> United Arab Emirates
Referencia: Benin
Referencias Similares:
--> Qatar
--> Martinique
--> Hong Kong
Referenci

/tmp/ipykernel_2533/4098855849.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  similares = similares.append({'referencia': row['referencia'], 'vizinho': rw['referencia']}, ignore_index = True)
/tmp/ipykernel_2533/4098855849.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  similares = similares.append({'referencia': row['referencia'], 'vizinho': rw['referencia']}, ignore_index = True)
/tmp/ipykernel_2533/4098855849.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  similares = similares.append({'referencia': row['referencia'], 'vizinho': rw['referencia']}, ignore_index = True)
/tmp/ipykernel_2533/4098855849.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future vers

--> Mauritania
--> Croatia
--> Togo
Referencia: United Arab Emirates
Referencias Similares:
--> Bahrain
--> Sri Lanka
--> Slovakia
Referencia: Gabon
Referencias Similares:
--> Tunisia
--> Guadeloupe
--> Slovenia
Referencia: Lebanon
Referencias Similares:
--> Namibia
--> Bosnia and Herzegovina
--> Djibouti
Referencia: Sierra Leone
Referencias Similares:
--> Central African Republic
--> Paraguay
--> Bosnia and Herzegovina
Referencia: Djibouti
Referencias Similares:
--> Bosnia and Herzegovina
--> Sierra Leone
--> Central African Republic
Referencia: Ethiopia
Referencias Similares:
--> Slovakia
--> Sri Lanka
--> Bahrain
Referencia: Equatorial Guinea
Referencias Similares:
--> Eritrea
--> Macedonia
--> Armenia
Referencia: Bahrain
Referencias Similares:
--> Sri Lanka
--> Slovakia
--> Ethiopia
Referencia: Chad
Referencias Similares:
--> Guadeloupe
--> Sri Lanka
--> Slovakia
Referencia: Eritrea
Referencias Similares:
--> Equatorial Guinea
--> Macedonia
--> Bahrain


/tmp/ipykernel_2533/4098855849.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  similares = similares.append({'referencia': row['referencia'], 'vizinho': rw['referencia']}, ignore_index = True)
/tmp/ipykernel_2533/4098855849.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  similares = similares.append({'referencia': row['referencia'], 'vizinho': rw['referencia']}, ignore_index = True)
/tmp/ipykernel_2533/4098855849.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  similares = similares.append({'referencia': row['referencia'], 'vizinho': rw['referencia']}, ignore_index = True)
/tmp/ipykernel_2533/4098855849.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future vers

referencia            vizinho
0       Mexico            Germany
1       Mexico              India
2       Mexico              China
3     Colombia       Saudi Arabia
4     Colombia              Egypt
..         ...                ...
436       Chad          Sri Lanka
437       Chad           Slovakia
438    Eritrea  Equatorial Guinea
439    Eritrea          Macedonia
440    Eritrea            Bahrain

[441 rows x 2 columns]

In [19]:
similares.to_feather('database/knn_produto.feather')

In [20]:
## Aula 15 - KNN - Vizinhos mais próximos
original = fit_data(data, 'Sub-Category')
original = original.fillna(0)
base = original[variaveis]
vizinhos = NearestNeighbors(n_neighbors=min(4, len(base))).fit(base)
similares = pd.DataFrame()
for index, row in original.iterrows():
    print('Referencia: {0}'.format(row['referencia']))
    print('Referencias Similares:')
    original_referencia = original[original['referencia'] == row['referencia']][variaveis]
    similar = vizinhos.kneighbors(original_referencia, return_distance=False)[0]
    original_similar = original.iloc[similar][variaveis].reset_index()
    referencia = original.iloc[similar]['referencia'].reset_index()
    referencia = referencia.merge(original_similar, on='index', how='left')
    referencia = referencia.drop(columns=['index'])
    for ind, rw in referencia.iterrows():    
        if row['referencia'] != rw['referencia']:            
            print('--> {0}'.format(rw['referencia']))
            similares = similares.append({'referencia': row['referencia'], 'vizinho': rw['referencia']}, ignore_index = True)
similares

similares.to_feather('database/knn_subcategoria.feather')

/tmp/ipykernel_2533/952877166.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rfm = rfm.append(
/tmp/ipykernel_2533/952877166.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rfm = rfm.append(
/tmp/ipykernel_2533/952877166.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rfm = rfm.append(
/tmp/ipykernel_2533/952877166.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rfm = rfm.append(
/tmp/ipykernel_2533/952877166.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rfm = rfm.append(
/tmp/ipykernel_2533/952877166.py:17: FutureWarning

Referencia: Labels
Referencias Similares:
--> Fasteners
--> Envelopes
--> Supplies
Referencia: Furnishings
Referencias Similares:
--> Art
--> Binders
--> Paper
Referencia: Bookcases
Referencias Similares:
--> Chairs
--> Copiers
--> Phones
Referencia: Binders
Referencias Similares:
--> Furnishings
--> Art
--> Paper
Referencia: Art
Referencias Similares:
--> Furnishings
--> Binders
--> Paper
Referencia: Envelopes
Referencias Similares:
--> Supplies
--> Paper
--> Fasteners
Referencia: Machines
Referencias Similares:
--> Accessories
--> Tables
--> Appliances
Referencia: Supplies
Referencias Similares:
--> Paper
--> Envelopes
--> Art
Referencia: Accessories
Referencias Similares:
--> Machines
--> Tables
--> Appliances
Referencia: Fasteners
Referencias Similares:
--> Labels
--> Envelopes
--> Supplies
Referencia: Chairs
Referencias Similares:
--> Bookcases
--> Copiers
--> Phones
Referencia: Copiers
Referencias Similares:
--> Bookcases
--> Chairs
--> Phones
Referencia: Storage
Referencias Simi

/tmp/ipykernel_2533/580077773.py:19: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  similares = similares.append({'referencia': row['referencia'], 'vizinho': rw['referencia']}, ignore_index = True)
/tmp/ipykernel_2533/580077773.py:19: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  similares = similares.append({'referencia': row['referencia'], 'vizinho': rw['referencia']}, ignore_index = True)
/tmp/ipykernel_2533/580077773.py:19: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  similares = similares.append({'referencia': row['referencia'], 'vizinho': rw['referencia']}, ignore_index = True)
/tmp/ipykernel_2533/580077773.py:19: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version.

In [21]:
## Aula 15 - KNN - Vizinhos mais próximos
original = fit_data(data, 'Product Name')
original = original.fillna(0)
base = original[variaveis]
vizinhos = NearestNeighbors(n_neighbors=min(4, len(base))).fit(base)
similares = pd.DataFrame()
for index, row in original.iterrows():
    print('Referencia: {0}'.format(row['referencia']))
    print('Referencias Similares:')
    original_referencia = original[original['referencia'] == row['referencia']][variaveis]
    similar = vizinhos.kneighbors(original_referencia, return_distance=False)[0]
    original_similar = original.iloc[similar][variaveis].reset_index()
    referencia = original.iloc[similar]['referencia'].reset_index()
    referencia = referencia.merge(original_similar, on='index', how='left')
    referencia = referencia.drop(columns=['index'])
    for ind, rw in referencia.iterrows():    
        if row['referencia'] != rw['referencia']:            
            print('--> {0}'.format(rw['referencia']))
            similares = similares.append({'referencia': row['referencia'], 'vizinho': rw['referencia']}, ignore_index = True)
similares

similares.to_feather('database/knn_produto.feather')

/tmp/ipykernel_2533/952877166.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rfm = rfm.append(
/tmp/ipykernel_2533/952877166.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rfm = rfm.append(
/tmp/ipykernel_2533/952877166.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rfm = rfm.append(
/tmp/ipykernel_2533/952877166.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rfm = rfm.append(
/tmp/ipykernel_2533/952877166.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rfm = rfm.append(
/tmp/ipykernel_2533/952877166.py:17: FutureWarning

Referencia: Hon File Folder Labels, Adjustable
Referencias Similares:
--> Newell 312
--> Wilson Jones Leather-Like Binders with DublLock Round Rings
--> Westinghouse Clip-On Gooseneck Lamps
Referencia: Tenex Clock, Durable
Referencias Similares:
--> Enermax Mouse, Erganomic
--> BIC Pencil Sharpener, Fluorescent
--> Advantus Clock, Black
Referencia: Ikea 3-Shelf Cabinet, Mobile
Referencias Similares:
--> Nokia Speaker Phone, with Caller ID
--> Cisco Speaker Phone, VoIP
--> Novimex Steel Folding Chair, Black
Referencia: Cardinal Binder, Clear
Referencias Similares:
--> Stockwell Push Pins, 12 Pack
--> GlobeWeis Manila Envelope, Recycled
--> BIC Pens, Easy-Erase
Referencia: Sanford Canvas, Water Color
Referencias Similares:
--> Hon Steel Folding Chair, Black
--> Samsung Signal Booster, with Caller ID
--> Dania Floating Shelf Set, Pine
Referencia: GlobeWeis Mailers, with clear poly window
Referencias Similares:
--> Rubbermaid Door Stop, Durable
--> GlobeWeis Interoffice Envelope, Security-

/tmp/ipykernel_2533/1239801287.py:19: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  similares = similares.append({'referencia': row['referencia'], 'vizinho': rw['referencia']}, ignore_index = True)
/tmp/ipykernel_2533/1239801287.py:19: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  similares = similares.append({'referencia': row['referencia'], 'vizinho': rw['referencia']}, ignore_index = True)
/tmp/ipykernel_2533/1239801287.py:19: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  similares = similares.append({'referencia': row['referencia'], 'vizinho': rw['referencia']}, ignore_index = True)
/tmp/ipykernel_2533/1239801287.py:19: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future vers

--> Fellowes Trays, Wire Frame
--> Nokia Audio Dock, Cordless
--> Bush Corner Shelving, Metal
Referencia: Deflect-O Clock, Black
Referencias Similares:
--> O'Sullivan Living Dimensions 5-Shelf Bookcases
--> Barricks Training Table, Fully Assembled
--> Lesro Training Table, Fully Assembled
Referencia: HP Copy Machine, Color
Referencias Similares:
--> Hewlett Wireless Fax, Digital
--> KitchenAid Stove, Silver
--> Ikea Classic Bookcase, Traditional
Referencia: Rogers Box, Single Width
Referencias Similares:
--> SanDisk Flash Drive, USB
--> Belkin Mouse, Programmable
--> Rogers Box, Wire Frame
Referencia: Wilson Jones Binding Machine, Durable
Referencias Similares:
--> Advantus Frame, Black
--> StarTech Card Printer, Wireless
--> High-Back Leather Manager's Chair
Referencia: Stockwell Thumb Tacks, Metal
Referencias Similares:
--> Stockwell Paper Clips, Metal
--> Stanley Highlighters, Blue
--> Stockwell Push Pins, Metal
Referencia: Motorola Office Telephone, with Caller ID
Referencias Simil

/tmp/ipykernel_2533/1239801287.py:19: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  similares = similares.append({'referencia': row['referencia'], 'vizinho': rw['referencia']}, ignore_index = True)
/tmp/ipykernel_2533/1239801287.py:19: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  similares = similares.append({'referencia': row['referencia'], 'vizinho': rw['referencia']}, ignore_index = True)
/tmp/ipykernel_2533/1239801287.py:19: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  similares = similares.append({'referencia': row['referencia'], 'vizinho': rw['referencia']}, ignore_index = True)
/tmp/ipykernel_2533/1239801287.py:19: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future vers

...

/tmp/ipykernel_2533/1239801287.py:19: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  similares = similares.append({'referencia': row['referencia'], 'vizinho': rw['referencia']}, ignore_index = True)
/tmp/ipykernel_2533/1239801287.py:19: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  similares = similares.append({'referencia': row['referencia'], 'vizinho': rw['referencia']}, ignore_index = True)
/tmp/ipykernel_2533/1239801287.py:19: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  similares = similares.append({'referencia': row['referencia'], 'vizinho': rw['referencia']}, ignore_index = True)
/tmp/ipykernel_2533/1239801287.py:19: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future vers

--> Xerox 1989
--> Grip Seal Envelopes
--> Xerox 20
Referencia: Acme Design Line 8" Stainless Steel Bent Scissors w/Champagne Handles, 3-1/8" Cut
Referencias Similares:
--> Acme Kleen Earth Office Shears
--> Newell 33
--> Black Avery Memo-Size 3-Ring Binder, 5 1/2" x 8 1/2"
Referencia: Star Micronics TSP100 TSP143LAN Receipt Printer
Referencias Similares:
--> Binney & Smith Highlighters, Easy-Erase
--> Global Italian Leather Office Chair
--> Elite Scissors, Serrated
Referencia: Xerox 1955
Referencias Similares:
--> Avery 500
--> Anker 24W Portable Micro USB Car Charger
--> Tenex Traditional Chairmats for Hard Floors, Average Lip, 36" x 48"
Referencia: Snap-A-Way Black Print Carbonless Speed Message, No Reply Area, Duplicate
Referencias Similares:
--> Xerox 1932
--> Xerox Blank Computer Paper
--> Vtech AT&T CL2940 Corded Speakerphone, Black
Referencia: 1/4 Fold Party Design Invitations & White Envelopes, 24 8-1/2" X 11" Cards, 25 Env./Pack
Referencias Similares:
--> Xerox 223
--> Ampad 

/tmp/ipykernel_2533/1239801287.py:19: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  similares = similares.append({'referencia': row['referencia'], 'vizinho': rw['referencia']}, ignore_index = True)
/tmp/ipykernel_2533/1239801287.py:19: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  similares = similares.append({'referencia': row['referencia'], 'vizinho': rw['referencia']}, ignore_index = True)
/tmp/ipykernel_2533/1239801287.py:19: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  similares = similares.append({'referencia': row['referencia'], 'vizinho': rw['referencia']}, ignore_index = True)
/tmp/ipykernel_2533/1239801287.py:19: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future vers

--> Jiffy Padded Mailers with Self-Seal Closure
--> Sony 8GB Class 10 Micro SDHC R40 Memory Card
--> SanDisk Cruzer 8 GB USB Flash Drive
Referencia: Hon Conference Table, Fully Assembled
Referencias Similares:
--> Panasonic KX MC6040 Color Laser Multifunction Printer
--> Global Leather & Oak Executive Chair, Burgundy
--> GE 2-Jack Phone Line Splitter


/tmp/ipykernel_2533/1239801287.py:19: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  similares = similares.append({'referencia': row['referencia'], 'vizinho': rw['referencia']}, ignore_index = True)
/tmp/ipykernel_2533/1239801287.py:19: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  similares = similares.append({'referencia': row['referencia'], 'vizinho': rw['referencia']}, ignore_index = True)
/tmp/ipykernel_2533/1239801287.py:19: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  similares = similares.append({'referencia': row['referencia'], 'vizinho': rw['referencia']}, ignore_index = True)
